In [2]:
!pip install -q jiwer==3.1.0
!pip install -q evaluate
!pip install -qU accelerate
!pip install -Uq torch
!pip install -q transformers[torch]
!pip install -q soundfile
!git clone https://github.com/SunbirdAI/salt.git
!pip install -qr salt/requirements.txt
!pip install -q peft
!pip install -q torchaudio torchvision

ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchaudio 2.7.0+cu128 requires torch==2.7.0, but you have torch 2.7.1 which is incompatible.
torchvision 0.22.0+cu128 requires torch==2.7.0, but you have torch 2.7.1 which is incompatible.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torchaudio 2.7.0+cu128 requires torch==2.7.0, but you have torch 2.6.0 which is incompatible.
torchvision 0.22.0+cu128 requires torch==2.7.0, but you have torch 2.6.0 which is incompatible.
Cloning into 'salt'...
remote: Enumerating objects: 1324, done.
remote: Counting objects: 100% (232/232), done.
remote: Compressing objects: 100% (136/136), done.
remote: Total 1324 (delta 138), reused 100 (delta 96), pack-reused 1092 (from 2)
Receiving objects: 100% (1

In [1]:
import os
from getpass import getpass
import yaml
import torch
import numpy as np
import datasets
import evaluate
import salt.dataset
import salt.metrics
import salt.constants
from salt.utils import DataCollatorCTCWithPadding as DataCollator
import transformers
from transformers import (
    AutoModelForCTC,
    AutoProcessor,
    TrainingArguments,
    Trainer
)
from transformers.models.wav2vec2.modeling_wav2vec2 import WAV2VEC2_ADAPTER_SAFE_FILE
from safetensors.torch import save_file as safe_save_file
import mlflow
import mlflow.pytorch
import huggingface_hub

In [2]:
# ==== Experiment flags ==== 
use_wandb = False
use_mlflow = True

# ==== MLflow setup ====
os.environ['MLFLOW_TRACKING_USERNAME'] = getpass('MLFLOW_TRACKING_USERNAME: ')
os.environ['MLFLOW_TRACKING_PASSWORD'] = getpass('MLFLOW_TRACKING_PASSWORD: ')
mlflow.set_tracking_uri('https://mlflow.sunbird.ai')

MLFLOW_TRACKING_USERNAME:  ········
MLFLOW_TRACKING_PASSWORD:  ········


In [5]:
yaml_config = f"""
pretrained_model: facebook/mms-1b-all
pretrained_adapter: kin
mlflow_experiment_name: kinyarwanda-asr
mlflow_run_name: sunbird-mms-kin-1b
adapter_save_id: kin

training_args:
  output_dir: stt-mms-kin
  per_device_train_batch_size: 24
  gradient_accumulation_steps: 2
  eval_strategy: steps
  max_steps: 60000
  gradient_checkpointing: True
  gradient_checkpointing_kwargs:
    use_reentrant: True
  fp16: True
  save_steps: 100
  eval_steps: 100
  logging_steps: 100
  learning_rate: 0.0003
  warmup_steps: 100
  save_total_limit: 2
  load_best_model_at_end: True
  metric_for_best_model: loss
  greater_is_better: False
  weight_decay: 0.01
  report_to: []

Wav2Vec2ForCTC_args:
  attention_dropout: 0.0
  hidden_dropout: 0.0
  feat_proj_dropout: 0.0
  layerdrop: 0.0
  ctc_loss_reduction: mean
  ignore_mismatched_sizes: True

train:
  huggingface_load:
    - path: jq/kinyarwanda-speech-hackathon
      split: train
    - path: jq/kinyarwanda-speech-hackathon
      split: dev_test[1000:]
      trust_remote_code: True
  source:
    type: speech
    language: [kin]
    preprocessing:
      - set_sample_rate:
          rate: 8000
          p: 0.1
      - set_sample_rate:
          rate: 16000
      - normalize_audio
      - augment_audio_speed:
          p: 0.2
          low: 0.95
          high: 1.15
      - augment_audio_noise:
          max_relative_amplitude: 0.5
          noise_audio_repo:
            path: Sunbird/urban-noise
            name: small
            split: train
  target:
    type: text
    language: [kin]
    preprocessing:
      - lower_case
      - clean_and_remove_punctuation:
          allowed_punctuation: "'"
  shuffle: True

validation:
  huggingface_load:
    - path: jq/kinyarwanda-speech-hackathon
      split: dev_test[:100]
  source:
    type: speech
    language: [kin]
    preprocessing:
      - set_sample_rate:
          rate: 16000
  target:
    type: text
    language: [kin]
    preprocessing:
      - lower_case
      - clean_and_remove_punctuation:
          allowed_punctuation: "'"
"""

In [6]:
config = yaml.safe_load(yaml_config)

# ==== Data Loading ==== 
train_ds = salt.dataset.create(config['train'], verbose=True)
valid_ds = salt.dataset.create(config['validation'], verbose=True)
salt.utils.show_dataset(train_ds, audio_features=['source'], N=5)

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

train-00025-of-00075.parquet:   0%|          | 0.00/499M [00:00<?, ?B/s]

train-00026-of-00075.parquet:   0%|          | 0.00/498M [00:00<?, ?B/s]

train-00027-of-00075.parquet:   0%|          | 0.00/499M [00:00<?, ?B/s]

...

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

jq/kinyarwanda-speech-hackathon: 261657 rows
jq/kinyarwanda-speech-hackathon: 8263 rows
Total rows: 269920


README.md:   0%|          | 0.00/2.03k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/48.5M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/1000 [00:00<?, ? examples/s]

In [7]:
# ==== Processor / Tokenizer ==== 
processor = AutoProcessor.from_pretrained(config['pretrained_model'])
feature_extractor = processor.feature_extractor
tokenizer = processor.tokenizer


# ==== Data Collator ==== 
data_collator = DataCollator(processor=processor, padding=True)

preprocessor_config.json:   0%|          | 0.00/254 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/397 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.34M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/96.0 [00:00<?, ?B/s]

In [8]:
# ==== Dataset Preparation ==== 
def prepare_dataset(batch):
    # Extract input features
    batch['input_values'] = processor(batch['source'], sampling_rate=16000).input_values
    # Tokenize labels
    batch['labels'] = processor.tokenizer(batch['target']).input_ids
    return batch

train_data = train_ds.map(prepare_dataset, batched=True, remove_columns=['source','target'])
val_data = valid_ds.map(prepare_dataset, batched=True, remove_columns=['source','target'])


In [9]:
# ==== Metrics ==== 
compute_metrics = salt.metrics.multilingual_eval_fn(
    valid_ds,
    [evaluate.load('wer'), evaluate.load('cer')],
    tokenizer,
    log_first_N_predictions=2,
    speech_processor=processor
)

# ==== Model Setup ==== 
model = AutoModelForCTC.from_pretrained(
    config['pretrained_model'],
    pad_token_id=tokenizer.pad_token_id,
    vocab_size=len(tokenizer),
    **config['Wav2Vec2ForCTC_args']
)


Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

jq/kinyarwanda-speech-hackathon: 100 rows
Total rows: 100


config.json:   0%|          | 0.00/2.04k [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/3.86G [00:00<?, ?B/s]

In [10]:
# Load or init adapter
if config.get('pretrained_adapter'):
    model.load_adapter(config['pretrained_adapter'])
else:
    model.init_adapter_layers()

# Freeze base and train only adapter weights
model.freeze_base_model()
adapters = model._get_adapters()
for p in adapters.values():
    p.requires_grad = True


Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


(…)484fa50b63903c17c08ff761bba0d7062f1d80cd:   0%|          | 0.00/9.36M [00:00<?, ?B/s]

In [11]:
# ==== Training Arguments ==== 
report_to = []
if use_wandb: report_to.append('wandb')
if use_mlflow: report_to.append('mlflow')
config['training_args']['report_to'] = report_to

tf_args = transformers.TrainingArguments(**config['training_args'])


In [12]:
# ==== Trainer ==== 
trainer = Trainer(
    model=model,
    args=tf_args,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
    train_dataset=train_data,
    eval_dataset=val_data,
    tokenizer=feature_extractor,
    callbacks=[salt.utils.MlflowExtendedLoggingCallback()] if use_mlflow else None
)

# ==== MLflow Experiment ==== 
if use_mlflow:
    if not mlflow.get_experiment_by_name(config['mlflow_experiment_name']):
        mlflow.create_experiment(config['mlflow_experiment_name'])
    mlflow.set_experiment(config['mlflow_experiment_name'])


/tmp/ipykernel_2342/1255316063.py:2: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Trainer.__init__`. Use `processing_class` instead.
  trainer = Trainer(


In [ ]:
# ==== Run Training ==== 
with mlflow.start_run(run_name=config['mlflow_run_name'], log_system_metrics=use_mlflow) as run:
    mlflow.log_params(config)
    trainer.train()
    metrics = trainer.evaluate()
    trainer.save_model()

    # Save adapter weights
    adapter_file = WAV2VEC2_ADAPTER_SAFE_FILE.format(config['adapter_save_id'])
    adapter_path = os.path.join(tf_args.output_dir, adapter_file)
    safe_save_file(model._get_adapters(), adapter_path, metadata={"format": "pt"})

    # Log artifacts
    mlflow.log_artifact(os.path.join(tf_args.output_dir, 'preprocessor_config.json'), artifact_path='model_artifacts')
    mlflow.log_artifact(os.path.join(tf_args.output_dir, 'training_args.bin'), artifact_path='model_artifacts')
    mlflow.log_artifact(adapter_path, artifact_path='model_artifacts')


2025/06/24 00:10:45 INFO mlflow.system_metrics.system_metrics_monitor: Skip logging GPU metrics. Set logger level to DEBUG for more details.
2025/06/24 00:10:45 INFO mlflow.system_metrics.system_metrics_monitor: Started monitoring system metrics.


Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

Loading dataset shards:   0%|          | 0/74 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

...

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

jq/kinyarwanda-speech-hackathon: 100 rows
Total rows: 100
First N predictions in eval set:
Prediction (kin to kin): "umugore wambaye umupira w'akazi muzankano irimu ibara ry'umuhondo handitse amagambo yandikishije ibara ry'ubururu afite igikoresho cy'ituma naho gikoreshwa mu guhamagara no kwandika ubutumwa bugufi", True label: "umugore wambaye umupira w'akazi mpuzankano iri mu ibara ry'umuhondo handitseho amagambo yandikishije ibara ry'ubururu afite igikoresho cy'itumanaho gikoreshwa mu guhamagara no kwandika ubutumwa bugufi"
Prediction (kin to kin): "uburyo emutiyeni yatangije wishyura amafaranga kuri terefone ukoresheje cyangwa mudasobwa batagize amafaranga n'amake bagukata wohereza", True label: "uburyo emutiyene yatangije wishyura amafaranga kuri terefone ukoresheje cyangwa mudasobwa batagize amafaranga na make bagukata wohereza"


Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/75 [00:00<?, ?it/s]

jq/kinyarwanda-speech-hackathon: 100 rows
Total rows: 100
First N predictions in eval set:
Prediction (kin to kin): "umugore wambaye umupira wakazi muzankano irimu ibara ry'umuhondo handitse amagambo yandikishije ibara ry'ubururu afite igikoresho cy'itumanaho gikoreshwa mu guhamagara no kwandika ubutumwa bugufi", True label: "umugore wambaye umupira w'akazi mpuzankano iri mu ibara ry'umuhondo handitseho amagambo yandikishije ibara ry'ubururu afite igikoresho cy'itumanaho gikoreshwa mu guhamagara no kwandika ubutumwa bugufi"
Prediction (kin to kin): "uburyo emutiyeni yatangije wishyura amafaranga kuri terefone ukoresheje cyangwa mudasobwa batagize amafaranga n'amake bagukata wohereza", True label: "uburyo emutiyene yatangije wishyura amafaranga kuri terefone ukoresheje cyangwa mudasobwa batagize amafaranga na make bagukata wohereza"


In [ ]:
# ==== Push to Hub ==== 
processor.push_to_hub(tf_args.output_dir, private=True)
model.push_to_hub(tf_args.output_dir, private=True)
